In [29]:
# conda install scikit-learn
# install from: http://docs.python-requests.org/en/master/
# to fix ssl installation of python packages issue
# curl https://bootstrap.pypa.io/get-pip.py | python3
# instructions to setup virtualenv
# https://www.tensorflow.org/install/install_mac
# pip3 install -r requirements.txt
# https://www.datacamp.com/community/tutorials/tensorflow-tutorial
# https://github.com/jtopor/CUNY-MSDA-661/blob/master/CIFAR-100/TF-Layers-CIFAR-100-v2.py
# feature columns
# https://data-flair.training/blogs/tensorflow-wide-and-deep-learning/
# import saved model
# https://stackoverflow.com/a/46139198
# https://medium.com/@zhanwenchen/export-and-import-models-with-tensorflow-savedmodelbuilder-an-lstm-example-9095d836a23a

from __future__ import absolute_import
from __future__ import division
from __future__ import print_function

import requests
import cv2
import h5py
import scipy.misc
import numpy as np
import csv
import sklearn.model_selection as model
import pickle 
import tensorflow as tf

from csv import DictReader
from urllib.request import urlopen
from matplotlib.pyplot import imshow
from fr_utils import *
from inception_blocks_v2 import *
from skimage import transform
from tensorflow.contrib import learn
from tensorflow.contrib.learn.python.learn.estimators import model_fn as model_fn_lib
from tensorflow.contrib import predictor

%matplotlib inline
%load_ext autoreload
%autoreload

learning_rate = 0.001
IMAGE_HEIGHT = 32
IMAGE_WIDTH = 32
IMAGE_DEPTH = 3
model_ckpt_dir = "./models/cifar-100"
model_prefix = "model.ckpt-5240"
saved_models_dir = "saved_models/cifar-100"

np.set_printoptions(threshold=np.nan)

The autoreload extension is already loaded. To reload it, use:
  %reload_ext autoreload


In [2]:
def convert_input_format(data):    
    return np.transpose(
        np.reshape(data, (-1, 32, 32, 3), order="F"),
        axes=(0, 2, 1, 3)
    )

def convert_output_labels(data):
    return np.asarray(data['fine_labels'], dtype=np.int32)

def one_hot_labels(labels):
    return tf.one_hot(indices=tf.cast(labels, tf.int32), depth=100)

def unpickle(file):
    fo = open(file, "rb")
    dict = pickle.load(fo, encoding="latin1")
    fo.close()
    return dict

In [3]:
def conv_layer(input_layer, filters=32, kernel_size=[5,5]):
    # setting up the conv layer, with stride and padding
    return tf.layers.conv2d(
        inputs=input_layer,
        filters=filters,
        kernel_size=kernel_size,
        padding="same",
        activation=tf.nn.relu
    )

def maxpool_layer(conv, pool_size=[2,2], strides=2):
    return tf.layers.max_pooling2d(
        inputs=conv, pool_size=pool_size, strides=strides
    )

def dropout_layer(inputs, mode, rate=0.25):
    
    return tf.layers.dropout(
        inputs=inputs, rate=rate, training=mode == learn.ModeKeys.TRAIN
    )

def dense_layer(inputs, units, activation=tf.nn.relu):
    return tf.layers.dense(inputs=inputs, units=units, activation=activation)

def determine_loss(labels, logits, mode):
    print(mode)
#     if mode != learn.ModeKeys.INFER:
    return tf.losses.softmax_cross_entropy (
        onehot_labels=one_hot_labels(labels),
        logits=logits
    )
#     else:
#         return None
    
def determine_train_op(loss, mode):
    print(mode)
#     if mode == learn.ModeKeys.TRAIN:
    return tf.contrib.layers.optimize_loss (
        loss=loss, 
        global_step=tf.contrib.framework.get_global_step(),
        learning_rate=0.0001,
        optimizer="Adam"
    )
#     else:
#         return None
    
def generate_predictions(logits):
    return {
        "classes": tf.argmax(input=logits, axis=1),
        "probabilities": tf.nn.softmax(logits, name="softmax_tensor")
    }

def cnn_model(features, labels, mode): 
    mode = learn.ModeKeys.TRAIN if mode == "train" else learn.ModeKeys.INFER
    input_layer = tf.convert_to_tensor(features)
    
    # cnn layer 1
    conv1 = conv_layer(input_layer)
    conv2 = conv_layer(conv1)
    
    # pooling layer 1 
    pool1 = maxpool_layer(conv2)
    
    # dropout operation
    dropout1 = dropout_layer(pool1, mode)
    
    # cnn layer 2 
    conv3 = conv_layer(dropout1, 64, [3, 3])
    conv4 = conv_layer(conv3, 64, [3, 3])
    
    # pooling layer 2
    pool2 = maxpool_layer(conv4)
    
    # dropout operation
    dropout2 = dropout_layer(pool2, mode)
    
    # flatten tensor into a batch of vectors
    pool2_flat = tf.reshape(dropout2, [-1, 8 * 8 * 64])
    
    # dense layer 
    dense1 = dense_layer(pool2_flat, 1024)
    
    # flatten tensor again
    dropout3 = dropout_layer(dense1, mode, 0.4)
    
    # second fully connected layer 
    dense2 = tf.layers.dense(inputs=dropout3, units=512)
    
    # dropout operation
    dropout4 = dropout_layer(dense2, mode, 0.4)
    
    # logits layer
    logits = tf.layers.dense(inputs=dropout4, units=100)
    
    loss = determine_loss(labels, logits, mode)
    train_op = determine_train_op(loss, mode)
    predictions = generate_predictions(logits)
    
    return model_fn_lib.ModelFnOps(
        mode=mode, predictions=predictions, loss=loss, train_op=train_op
    )


In [30]:
def generate_accuracy_metric():
    # configure the accuracy metric
    return {
        "accuracy": learn.MetricSpec (
            metric_fn=tf.metrics.accuracy, prediction_key="classes"
        )
    }

def serving_input_fn():
    """An input receiver that expects a serialized tf.Example."""

    # feature spec dictionary  determines our input parameters for the model
    feature_spec = {
        'images': tf.FixedLenFeature(shape=[1], dtype=tf.float32)
    }

    # the inputs will be initially fed as strings with data serialized by
    # Google ProtoBuffers
    serialized_tf_example = tf.placeholder(
        dtype=tf.string, shape=[1], name='input_example_tensor')
    receiver_tensors = {'images': serialized_tf_example}

    # deserialize input
    features = tf.parse_example(serialized_tf_example, feature_spec)
    return tf.estimator.export.ServingInputReceiver(features, receiver_tensors)
    
def print_evaluate_model(cifar_classifier, data, labels, epoches, subset):
    small_train = np.array_split(data, epoches)[subset]
    small_labels = np.array_split(labels, epoches)[subset]
    evaluate_results = cifar_classifier.evaluate(
        x=small_train, y=small_labels, metrics=generate_accuracy_metric()
    )
    print(evaluate_results)
    return evaluate_results

def setup_and_train_model():
    dataset = unpickle("./datasets/cifar-100-parsed/cifar-100-python/train")
    data = dataset["data"]
    data = data.astype("float32")
    train_data = convert_input_format(data)
    train_labels = convert_output_labels(dataset)
    
    deep_columns = [
        tf.feature_column.numeric_column('beaver'),
        tf.feature_column.numeric_column('dolphin'),
        tf.feature_column.numeric_column('otter'),
        tf.feature_column.numeric_column('seal'),
        tf.feature_column.numeric_column('whale'),
        tf.feature_column.numeric_column('aquarium fish'),
        tf.feature_column.numeric_column('flatfish'),
        tf.feature_column.numeric_column('ray'),
        tf.feature_column.numeric_column('shark'),
        tf.feature_column.numeric_column('trout'),
        tf.feature_column.numeric_column('orchids'),
        tf.feature_column.numeric_column('poppies'),
        tf.feature_column.numeric_column('roses'),
        tf.feature_column.numeric_column('sunflowers'),
        tf.feature_column.numeric_column('sunflowers'),
        tf.feature_column.numeric_column('bottles'),
        tf.feature_column.numeric_column('bowls'),
        tf.feature_column.numeric_column('cans'),
        tf.feature_column.numeric_column('cups'),
        tf.feature_column.numeric_column('plates'),
        tf.feature_column.numeric_column('apples'),
        tf.feature_column.numeric_column('mushrooms'),
        tf.feature_column.numeric_column('oranges'),
        tf.feature_column.numeric_column('pears'),
        tf.feature_column.numeric_column('sweet peppers'),
        tf.feature_column.numeric_column('clock'),
        tf.feature_column.numeric_column('computer keyboard'),
        tf.feature_column.numeric_column('lamp'),
        tf.feature_column.numeric_column('telephone'),
        tf.feature_column.numeric_column('television'),
        tf.feature_column.numeric_column('bed'),
        tf.feature_column.numeric_column('chair'),
        tf.feature_column.numeric_column('couch'),
        tf.feature_column.numeric_column('table'),
        tf.feature_column.numeric_column('wardrobe'),
        tf.feature_column.numeric_column('bee'),
        tf.feature_column.numeric_column('beetle'),
        tf.feature_column.numeric_column('butterfly'),
        tf.feature_column.numeric_column('caterpillar'),
        tf.feature_column.numeric_column('cockroach'),
        tf.feature_column.numeric_column('bear'),
        tf.feature_column.numeric_column('leopard'),
        tf.feature_column.numeric_column('lion'),
        tf.feature_column.numeric_column('tiger'),
        tf.feature_column.numeric_column('wolf'),
        tf.feature_column.numeric_column('bridge'),
        tf.feature_column.numeric_column('castle'),
        tf.feature_column.numeric_column('house'),
        tf.feature_column.numeric_column('road'),
        tf.feature_column.numeric_column('skyscraper'),
        tf.feature_column.numeric_column('cloud'),
        tf.feature_column.numeric_column('forest'),
        tf.feature_column.numeric_column('mountain'),
        tf.feature_column.numeric_column('plain'),
        tf.feature_column.numeric_column('sea'),
        tf.feature_column.numeric_column('camel'),
        tf.feature_column.numeric_column('cattle'),
        tf.feature_column.numeric_column('chimpanzee'),
        tf.feature_column.numeric_column('elephant'),
        tf.feature_column.numeric_column('kangaroo'),
        tf.feature_column.numeric_column('fox'),
        tf.feature_column.numeric_column('porcupine'),
        tf.feature_column.numeric_column('possum'),
        tf.feature_column.numeric_column('raccoon'),
        tf.feature_column.numeric_column('skunk'),
        tf.feature_column.numeric_column('crab'),
        tf.feature_column.numeric_column('lobster'),
        tf.feature_column.numeric_column('snail'),
        tf.feature_column.numeric_column('spider'),
        tf.feature_column.numeric_column('worm'),
        tf.feature_column.numeric_column('baby'),
        tf.feature_column.numeric_column('boy'),
        tf.feature_column.numeric_column('girl'),
        tf.feature_column.numeric_column('man'),
        tf.feature_column.numeric_column('woman'),
        tf.feature_column.numeric_column('crocodile'),
        tf.feature_column.numeric_column('dinosaur'),
        tf.feature_column.numeric_column('lizard'),
        tf.feature_column.numeric_column('snake'),
        tf.feature_column.numeric_column('turtle'),
        tf.feature_column.numeric_column('hamster'),
        tf.feature_column.numeric_column('mouse'),
        tf.feature_column.numeric_column('rabbit'),
        tf.feature_column.numeric_column('shrew'),
        tf.feature_column.numeric_column('squirrel'),
        tf.feature_column.numeric_column('maple'),
        tf.feature_column.numeric_column('oak'),
        tf.feature_column.numeric_column('palm'),
        tf.feature_column.numeric_column('pine'),
        tf.feature_column.numeric_column('willow'),
        tf.feature_column.numeric_column('bicycle'),
        tf.feature_column.numeric_column('bus'),
        tf.feature_column.numeric_column('motorcycle'),
        tf.feature_column.numeric_column('pickup truck'),
        tf.feature_column.numeric_column('train'),
        tf.feature_column.numeric_column('lawn-mower'),
        tf.feature_column.numeric_column('rocket'),
        tf.feature_column.numeric_column('streetcar'),
        tf.feature_column.numeric_column('tank'),
        tf.feature_column.numeric_column('tractor')
    ]
    
    feature_spec = tf.feature_column.make_parse_example_spec(deep_columns)
    export_input_fn = tf.contrib.learn.build_parsing_serving_input_fn(feature_spec)
    
    exporter = tf.estimator.LatestExporter (
        name="Servo",
        serving_input_receiver_fn=export_input_fn,
        assets_extra=None,
        as_text=False,
        exports_to_keep=5
    )
    
    # create custom estimator
    cifar_classifier = learn.Estimator (
        model_fn=cnn_model, model_dir=model_ckpt_dir
    )
    
    # log predictions
    tensors_to_log = {"probabilities": "softmax_tensor"}
    logging_hook = tf.train.LoggingTensorHook (
        tensors=tensors_to_log, every_n_iter=100
    )
    
    # train the model
    with tf.device("/cpu:0"):
        cifar_classifier.fit (
            x=train_data,
            y=train_labels,
            batch_size=64, 
            steps=5240,
            monitors=[logging_hook]
        )
    
    full_model_dir = cifar_classifier.export_savedmodel(
        model_ckpt_dir, export_input_fn
    )
    return cifar_classifier


def test_model(cifar_classifier):
    dataset = unpickle("./datasets/cifar-100-parsed/cifar-100-python/test")
    data = dataset["data"][0:200]
    data = data.astype("float32")
    test_data = convert_input_format(data)
    test_labels = convert_output_labels(dataset)
    
    # evaluate all test data and print results
    acc = 0
    e_loss = 0
    n_batches = 20
    for i in range (0, n_batches - 1):
        small_eval =  np.array_split(test_data, n_batches)[i]
        small_labs =  np.array_split(test_labels, n_batches)[i]
        eval_results = cifar_classifier.evaluate(
          x=small_eval, y=small_labs, metrics=generate_accuracy_metric())
        print(eval_results)
        acc += eval_results["accuracy"]
        e_loss += eval_results["loss"]

    overall_acc = acc / n_batches
    overall_loss = e_loss/ n_batches
    print("Eval Accuracy = ", overall_acc)
    print("Eval Loss = ", overall_loss)
    return cifar_classifier
    
def export_saved_model():
    with tf.Session(graph=tf.Graph()) as sess:
        # restore from checkpoint
        loader = tf.train.import_meta_graph("models/cifar-100" + "/" + model_prefix + ".meta")
        loader.restore(sess, "models/cifar-100" + "/" + model_prefix)
        
        # export checkpoint to SavedModel
        builder = tf.saved_model.builder.SavedModelBuilder(saved_models_dir)
        builder.add_meta_graph_and_variables(sess, 
                                             [tf.saved_model.tag_constants.TRAINING],
                                             strip_default_attrs=True
                                            )
        
        builder.add_meta_graph([tf.saved_model.tag_constants.SERVING], strip_default_attrs=True)
        builder.save()
        
def import_saved_model():
    dataset = unpickle("./datasets/cifar-100-parsed/cifar-100-python/test")
    data = dataset["data"][201:500]
    data = data.astype("float32")
    test_data = convert_input_format(data)
    test_labels = convert_output_labels(dataset)
    
    predict_model = predictor.from_saved_model(saved_models_dir)
    predict_model = test_model(predict_model)
    predictions = predict_model({"x": test_data})
    print(predictions['scores'])


In [6]:
classifier = setup_and_train_model()

Instructions for updating:
Please use tf.estimator.export.build_parsing_serving_input_receiver_fn.
Instructions for updating:
Please replace uses of any Estimator from tf.contrib.learn with an Estimator from tf.estimator.*
Instructions for updating:
When switching to tf.estimator.Estimator, use tf.estimator.RunConfig instead.
INFO:tensorflow:Using default config.
INFO:tensorflow:Using config: {'_master': '', '_keep_checkpoint_every_n_hours': 10000, '_num_ps_replicas': 0, '_task_id': 0, '_environment': 'local', '_session_config': None, '_model_dir': './models/cifar-100', '_task_type': None, '_num_worker_replicas': 0, '_is_chief': True, '_save_checkpoints_steps': None, '_tf_config': gpu_options {
  per_process_gpu_memory_fraction: 1.0
}
, '_save_checkpoints_secs': 600, '_device_fn': None, '_evaluation_master': '', '_train_distribute': None, '_tf_random_seed': None, '_cluster_spec': <tensorflow.python.training.server_lib.ClusterSpec object at 0x13833cb00>, '_keep_checkpoint_max': 5, '_log

INFO:tensorflow:loss = 121.80063, step = 1
INFO:tensorflow:global_step/sec: 2.36487
INFO:tensorflow:probabilities = [[0.00719178 0.00755512 0.00999516 0.013061   0.01331975 0.01582197
  0.00543297 0.00714943 0.00844775 0.01566626 0.00975777 0.00993321
  0.00803557 0.01202097 0.00527248 0.01000019 0.00936812 0.00481
  0.00549443 0.00873515 0.00866618 0.00963791 0.01157883 0.00752883
  0.00773323 0.00933842 0.01002822 0.0098968  0.00836333 0.00994418
  0.00644571 0.01097158 0.00845584 0.01668172 0.01104576 0.01150851
  0.00859081 0.00675332 0.00391042 0.01960835 0.01664373 0.01063966
  0.0055666  0.00813861 0.00803138 0.0106048  0.00979328 0.00856457
  0.00920061 0.00632583 0.01634014 0.00958679 0.01451402 0.01603008
  0.00680067 0.00710004 0.01852519 0.00556024 0.0101379  0.00659194
  0.01244426 0.00868943 0.01642114 0.01627837 0.01409456 0.00722195
  0.00333281 0.00364247 0.00965876 0.00934583 0.02054644 0.0072925
  0.02293475 0.01145543 0.01113752 0.01005356 0.0156281  0.00629241
  0.

INFO:tensorflow:loss = 4.774393, step = 101 (42.203 sec)
INFO:tensorflow:global_step/sec: 2.43677
INFO:tensorflow:probabilities = [[0.00823701 0.01011674 0.00794484 0.01067056 0.01102315 0.01019394
  0.01199905 0.00663969 0.01029368 0.0092535  0.00780759 0.01124871
  0.01025505 0.01076548 0.01001106 0.00990287 0.01044448 0.00946953
  0.00940358 0.01146387 0.00810365 0.01276813 0.01100126 0.00867933
  0.01109327 0.00800399 0.00929633 0.00798549 0.01073566 0.01195851
  0.00796144 0.00810969 0.01170156 0.0082873  0.00913082 0.01228208
  0.01265612 0.01214168 0.00837381 0.01350958 0.0076149  0.01181711
  0.00964348 0.01058136 0.01072466 0.01158145 0.01326657 0.00743716
  0.01043996 0.00850435 0.00996102 0.01139888 0.01022557 0.01317895
  0.01085968 0.01120077 0.00861123 0.00962777 0.00709424 0.01207348
  0.00788375 0.01106047 0.00832269 0.01456141 0.00758624 0.00807279
  0.01110786 0.01091263 0.01044462 0.00960765 0.00660801 0.00778042
  0.00712469 0.01346041 0.00616317 0.01230663 0.010135

INFO:tensorflow:loss = 4.597822, step = 201 (41.036 sec)
INFO:tensorflow:global_step/sec: 2.31141
INFO:tensorflow:probabilities = [[0.00848852 0.00999233 0.00977816 0.01011734 0.01030866 0.00893208
  0.00974779 0.011989   0.00958559 0.01041604 0.01223985 0.01116914
  0.00933249 0.00920978 0.00862707 0.01107048 0.00799173 0.01057556
  0.01006565 0.0076885  0.01164654 0.00994806 0.00930199 0.00834498
  0.01004007 0.01230714 0.01215009 0.00995983 0.01069839 0.01041477
  0.00940825 0.01044845 0.00943605 0.01050166 0.01199408 0.00885825
  0.00968108 0.00957391 0.01073827 0.01002261 0.00924674 0.01051459
  0.00898833 0.0072852  0.01006983 0.00741728 0.01071772 0.00856225
  0.00979509 0.01160242 0.00979132 0.01071232 0.01208692 0.00769418
  0.01009956 0.01060613 0.00933161 0.00846222 0.00963652 0.01157217
  0.00970951 0.00948228 0.00926738 0.01049626 0.00842452 0.0104645
  0.00945422 0.00885713 0.01183943 0.01208998 0.00921718 0.01090775
  0.01013202 0.00781698 0.0119919  0.00915474 0.0094884

INFO:tensorflow:loss = 4.6132507, step = 301 (43.266 sec)
INFO:tensorflow:global_step/sec: 2.38604
INFO:tensorflow:probabilities = [[0.00735538 0.01112664 0.00743953 0.01172226 0.01021113 0.00622585
  0.00848572 0.01276136 0.01464072 0.01018758 0.01014361 0.01301251
  0.00719539 0.0084106  0.01189043 0.01035351 0.01083675 0.01072569
  0.0083558  0.00989538 0.00867663 0.00581368 0.01108742 0.00699878
  0.01236571 0.01245878 0.0092142  0.00981387 0.00881579 0.00772865
  0.00758681 0.00783866 0.0114184  0.01202245 0.01444075 0.01304324
  0.00937021 0.01092702 0.0125415  0.01202956 0.01027857 0.01457006
  0.01338377 0.00719538 0.00880971 0.00912541 0.00836256 0.00804982
  0.00929119 0.01431315 0.00969572 0.01189979 0.01633268 0.01042556
  0.01036754 0.00786505 0.00819662 0.01079219 0.01171919 0.01334251
  0.01364336 0.00838294 0.00722237 0.01428168 0.0121368  0.0079839
  0.01218689 0.00572541 0.00999586 0.00500375 0.00724364 0.00875668
  0.01745134 0.01019422 0.00892964 0.0069013  0.012305

...

INFO:tensorflow:loss = 3.4975069, step = 4901 (52.404 sec)
INFO:tensorflow:global_step/sec: 2.16096
INFO:tensorflow:probabilities = [[0.00021714 0.00791825 0.00275624 0.00184954 0.00183303 0.0009639
  0.00103636 0.00170566 0.00313786 0.00045091 0.00199353 0.00095802
  0.02370202 0.00193986 0.00022047 0.00193461 0.00088007 0.00324065
  0.00271629 0.00130093 0.00072527 0.00087074 0.00040298 0.00551118
  0.00112343 0.00032911 0.00217941 0.00402563 0.00216562 0.00300396
  0.13996966 0.00300682 0.00508462 0.00132627 0.00089671 0.00056409
  0.00044862 0.00191443 0.00100359 0.01109108 0.00656044 0.00066159
  0.00028638 0.0003096  0.00315766 0.00103042 0.00203387 0.00039376
  0.00073629 0.07875713 0.00114054 0.00040658 0.00041262 0.00038242
  0.00029145 0.00990317 0.01822675 0.00060272 0.00126934 0.00395497
  0.00036371 0.00196755 0.0002571  0.00296157 0.00268815 0.00332999
  0.0014044  0.06022057 0.00326459 0.01727569 0.00070837 0.01272247
  0.01911772 0.15413858 0.0013     0.0028043  0.01293

INFO:tensorflow:loss = 3.6154108, step = 5001 (46.276 sec)
INFO:tensorflow:global_step/sec: 2.19245
INFO:tensorflow:probabilities = [[0.01297046 0.00023962 0.0066304  0.00340195 0.00034369 0.00361431
  0.00066511 0.00367565 0.00501569 0.00796669 0.01934573 0.05110316
  0.00106916 0.00033438 0.00046379 0.00084484 0.0355201  0.00019113
  0.00161068 0.00056279 0.4754482  0.00046901 0.01310172 0.00551602
  0.02080573 0.00957541 0.00742691 0.00182724 0.05977201 0.00464477
  0.00032799 0.00029824 0.00845359 0.00056676 0.00045218 0.00228706
  0.0087445  0.00040796 0.00036093 0.00652967 0.02576501 0.00063806
  0.00017605 0.00029194 0.00597114 0.00612622 0.00124061 0.00040887
  0.0008038  0.00009376 0.00426497 0.00026006 0.00031346 0.00525738
  0.00065629 0.00060804 0.0001315  0.00470095 0.00093724 0.00087703
  0.00192818 0.00531357 0.00072508 0.00088088 0.00122647 0.00878154
  0.00057538 0.00466037 0.00305852 0.00153944 0.00310498 0.00720865
  0.00318484 0.00105154 0.0006578  0.00118029 0.0015

INFO:tensorflow:loss = 3.6184359, step = 5101 (45.635 sec)
INFO:tensorflow:global_step/sec: 1.767
INFO:tensorflow:probabilities = [[0.00170103 0.00376504 0.00444097 0.02528121 0.02346784 0.00421137
  0.00586498 0.00939873 0.02671131 0.00382869 0.00399648 0.00577037
  0.00793101 0.00776079 0.00665156 0.01199474 0.00876425 0.00474802
  0.02150767 0.02035988 0.00356322 0.01853281 0.00322167 0.00079487
  0.00467081 0.00362768 0.00721155 0.02547292 0.00222186 0.03214863
  0.00230242 0.03482496 0.00845789 0.00958544 0.01348268 0.00437678
  0.00546115 0.00783977 0.05018421 0.00835461 0.00242224 0.00945724
  0.02319731 0.01943602 0.01546317 0.00843551 0.00362325 0.00168757
  0.01689083 0.00111744 0.01092697 0.01055305 0.00428288 0.00097558
  0.0028573  0.01603505 0.00985594 0.00474512 0.01463252 0.004967
  0.00071838 0.00253645 0.00090688 0.01895808 0.00962753 0.00701341
  0.03756534 0.00606164 0.00140993 0.00278581 0.00160662 0.00139812
  0.01244332 0.0032157  0.03638861 0.02398989 0.00118681

INFO:tensorflow:loss = 3.8347726, step = 5201 (57.360 sec)
INFO:tensorflow:Saving checkpoints for 5240 into ./models/cifar-100/model.ckpt.
INFO:tensorflow:Loss for final step: 3.7432196.
Instructions for updating:
Switch to tf.estimator.Exporter and associated utilities.
Instructions for updating:
Switch to tf.estimator.Exporter and associated utilities.
Instructions for updating:
Switch to tf.estimator.Exporter and associated utilities.


TypeError: Failed to convert object of type <class 'dict'> to Tensor. Contents: {'tank': <tf.Tensor 'ParseExample/ParseExample:85' shape=(?, 1) dtype=float32>, 'telephone': <tf.Tensor 'ParseExample/ParseExample:86' shape=(?, 1) dtype=float32>, 'apples': <tf.Tensor 'ParseExample/ParseExample:0' shape=(?, 1) dtype=float32>, 'baby': <tf.Tensor 'ParseExample/ParseExample:2' shape=(?, 1) dtype=float32>, 'plates': <tf.Tensor 'ParseExample/ParseExample:61' shape=(?, 1) dtype=float32>, 'squirrel': <tf.Tensor 'ParseExample/ParseExample:80' shape=(?, 1) dtype=float32>, 'rocket': <tf.Tensor 'ParseExample/ParseExample:69' shape=(?, 1) dtype=float32>, 'lion': <tf.Tensor 'ParseExample/ParseExample:43' shape=(?, 1) dtype=float32>, 'house': <tf.Tensor 'ParseExample/ParseExample:38' shape=(?, 1) dtype=float32>, 'worm': <tf.Tensor 'ParseExample/ParseExample:98' shape=(?, 1) dtype=float32>, 'mouse': <tf.Tensor 'ParseExample/ParseExample:50' shape=(?, 1) dtype=float32>, 'castle': <tf.Tensor 'ParseExample/

In [31]:
export_saved_model()

INFO:tensorflow:Restoring parameters from models/cifar-100/model.ckpt-5240


AssertionError: Export directory already exists. Please specify a different export directory: saved_models/cifar-100

In [32]:
import_saved_model()

INFO:tensorflow:Restoring parameters from saved_models/cifar-100/variables/variables


ValueError: Got signature_def_key "serving_default". Available signatures are []. Original error:
No SignatureDef with key 'serving_default' found in MetaGraphDef.